In [83]:
#! /usr/bin/python3

from nltk import pos_tag

import sys
from os import listdir

from xml.dom.minidom import parse
from nltk.tokenize import word_tokenize
from nltk import pos_tag
from nltk.stem import WordNetLemmatizer

In [94]:
advice_clues = ["should", "may", "could", "would"]
effect_clues = ["administered", "concurrently", "concomitantly", "increase", "increases", "increased", "effect",
                "effects", "prevent", "prevents", "prevented", "potentiate", "potentiates", "potentiated"]
mechanism_clues = ["inhibit", "reduce", "reduces", "reduced", "decrease", "decreases", "decreased", "change",
                    "changes", "changed","elevate", "elevates", "elevated", "interfere", "interferes", "interfered"]

## -------------------
## -- check if a pair has an interaction, of which type
def check_interaction(tokens,entities,e1,e2) :
   ## Complete this function to return a pair (boolean, ddi_type)
   ## depending on whether there is an interaction between e1 and e2
    pos_tags = pos_tag([t[0] for t in tokens])
    lemmas = [wnl.lemmatize(t[0]) for t in tokens]
    before = []
    inBetween = []
    after = []
    isInBetween = False
    isBefore = True
    isAfter = False
    for k in range(len(tokens)):
        t = [tokens[k][0], tokens[k][1], tokens[k][2], pos_tags[k][1], lemmas[k]]
        if str(t[1]) == entities[e1][0]:
            isBefore = False
            isInBetween = True
        elif str(t[1]) == entities[e2][0]:
            isInBetween = False
            isAfter = True
        elif isBefore:
            before.append(t)
        elif isInBetween:
            inBetween.append(t)
        elif isAfter:
            after.append(t)
    if any(e in effect_clues for e in [t[4] for t in inBetween]):
        print(tokens)
        print(entities)
        print(inBetween)
        return True,"effect"
    if 'MD' in [t[3] for t in inBetween]: return True,"advise"

    return False,"null"

   
## --------- tokenize sentence ----------- 
## -- Tokenize sentence, returning tokens and span offsets

def tokenize(txt):
    offset = 0
    tks = []
    for t in word_tokenize(txt):
        offset = txt.find(t, offset)
        tks.append((t, offset, offset+len(t)-1))
        offset += len(t)
    return tks



In [91]:
pos_tag(['This', 'may', 'be', 'taken', 'before', 'that'])

[('This', 'DT'),
 ('may', 'MD'),
 ('be', 'VB'),
 ('taken', 'VBN'),
 ('before', 'IN'),
 ('that', 'DT')]

In [84]:
WordNetLemmatizer().lemmatize('inhibits')

'inhibits'

In [1]:
datadir = '../../../data/TEST-DDI/DrugBank/'

In [95]:
wnl = WordNetLemmatizer()
for f in listdir(datadir) :

    # parse XML file, obtaining a DOM tree
    tree = parse(datadir+"/"+f)

    # process each sentence in the file
    sentences = tree.getElementsByTagName("sentence")
    for s in sentences :
        sid = s.attributes["id"].value   # get sentence id
        stext = s.attributes["text"].value   # get sentence text

        tokens = tokenize(stext)
        
        # load sentence entities
        entities = {}
        ents = s.getElementsByTagName("entity")
        for e in ents :
           id = e.attributes["id"].value
           offs = e.attributes["charOffset"].value.split("-")           
           entities[id] = offs
        
        # for each pair in the sentence, decide whether it is DDI and its type
        pairs = s.getElementsByTagName("pair")
        for p in pairs:
           id_e1 = p.attributes["e1"].value
           id_e2 = p.attributes["e2"].value
           (is_ddi,ddi_type) = check_interaction(tokens,entities,id_e1,id_e2)
           ddi = "1" if is_ddi else "0"
           print(sid+"|"+id_e1+"|"+id_e2+"|"+ddi+"|"+ddi_type)


DDI-DrugBank.d507.s0|DDI-DrugBank.d507.s0.e0|DDI-DrugBank.d507.s0.e1|0|null
[('The', 0, 2), ('administration', 4, 17), ('of', 19, 20), ('guanfacine', 22, 31), ('concomitantly', 33, 45), ('with', 47, 50), ('known', 52, 56), ('microsomal', 58, 67), ('enzyme', 69, 74), ('inducer', 76, 82), ('(', 84, 84), ('phenobarbital', 85, 97), ('or', 99, 100), ('phenytoin', 102, 110), (')', 111, 111), ('to', 113, 114), ('two', 116, 118), ('patients', 120, 127), ('with', 129, 132), ('renal', 134, 138), ('impairment', 140, 149), ('reportedly', 151, 160), ('resulted', 162, 169), ('in', 171, 172), ('significant', 174, 184), ('reductions', 186, 195), ('in', 197, 198), ('elimination', 200, 210), ('half-life', 212, 220), ('and', 222, 224), ('plasma', 226, 231), ('concentration', 233, 245), ('.', 246, 246)]
{'DDI-DrugBank.d507.s1.e0': ['22', '31'], 'DDI-DrugBank.d507.s1.e1': ['85', '97'], 'DDI-DrugBank.d507.s1.e2': ['102', '110']}
[['concomitantly', 33, 45, 'RB', 'concomitantly'], ['with', 47, 50, 'IN', 'with

[('Injection', 0, 8), (':', 9, 9), ('Lorazepam', 11, 19), ('injection', 21, 29), (',', 30, 30), ('like', 32, 35), ('other', 37, 41), ('injectable', 43, 52), ('benzodiazepines', 54, 68), (',', 69, 69), ('produces', 71, 78), ('depression', 80, 89), ('of', 91, 92), ('the', 94, 96), ('central', 98, 104), ('nervous', 106, 112), ('system', 114, 119), ('when', 121, 124), ('administered', 126, 137), ('with', 139, 142), ('ethyl', 144, 148), ('alcohol', 150, 156), (',', 157, 157), ('phenothiazines', 159, 172), (',', 173, 173), ('barbiturates', 175, 186), (',', 187, 187), ('MAO', 189, 191), ('inhibitors', 193, 202), (',', 203, 203), ('and', 205, 207), ('other', 209, 213), ('antidepressants.When', 215, 234), ('scopolamine', 236, 246), ('is', 248, 249), ('used', 251, 254), ('concomitantly', 256, 268), ('with', 270, 273), ('injectable', 275, 284), ('lorazepam', 286, 294), (',', 295, 295), ('an', 297, 298), ('increased', 300, 308), ('incidence', 310, 318), ('of', 320, 321), ('sedation', 323, 330), ('

DDI-DrugBank.d397.s8|DDI-DrugBank.d397.s8.e3|DDI-DrugBank.d397.s8.e7|0|null
DDI-DrugBank.d397.s8|DDI-DrugBank.d397.s8.e3|DDI-DrugBank.d397.s8.e8|0|null
DDI-DrugBank.d397.s8|DDI-DrugBank.d397.s8.e3|DDI-DrugBank.d397.s8.e9|0|null
DDI-DrugBank.d397.s8|DDI-DrugBank.d397.s8.e3|DDI-DrugBank.d397.s8.e10|0|null
DDI-DrugBank.d397.s8|DDI-DrugBank.d397.s8.e3|DDI-DrugBank.d397.s8.e11|0|null
DDI-DrugBank.d397.s8|DDI-DrugBank.d397.s8.e3|DDI-DrugBank.d397.s8.e12|0|null
DDI-DrugBank.d397.s8|DDI-DrugBank.d397.s8.e3|DDI-DrugBank.d397.s8.e13|0|null
DDI-DrugBank.d397.s8|DDI-DrugBank.d397.s8.e4|DDI-DrugBank.d397.s8.e5|0|null
DDI-DrugBank.d397.s8|DDI-DrugBank.d397.s8.e4|DDI-DrugBank.d397.s8.e6|0|null
DDI-DrugBank.d397.s8|DDI-DrugBank.d397.s8.e4|DDI-DrugBank.d397.s8.e7|0|null
DDI-DrugBank.d397.s8|DDI-DrugBank.d397.s8.e4|DDI-DrugBank.d397.s8.e8|0|null
DDI-DrugBank.d397.s8|DDI-DrugBank.d397.s8.e4|DDI-DrugBank.d397.s8.e9|0|null
DDI-DrugBank.d397.s8|DDI-DrugBank.d397.s8.e4|DDI-DrugBank.d397.s8.e10|0|null
DDI-Dru

DDI-DrugBank.d253.s3|DDI-DrugBank.d253.s3.e2|DDI-DrugBank.d253.s3.e3|0|null
DDI-DrugBank.d253.s3|DDI-DrugBank.d253.s3.e2|DDI-DrugBank.d253.s3.e4|0|null
DDI-DrugBank.d253.s3|DDI-DrugBank.d253.s3.e2|DDI-DrugBank.d253.s3.e5|0|null
DDI-DrugBank.d253.s3|DDI-DrugBank.d253.s3.e3|DDI-DrugBank.d253.s3.e4|0|null
DDI-DrugBank.d253.s3|DDI-DrugBank.d253.s3.e3|DDI-DrugBank.d253.s3.e5|0|null
DDI-DrugBank.d253.s3|DDI-DrugBank.d253.s3.e4|DDI-DrugBank.d253.s3.e5|0|null
DDI-DrugBank.d312.s1|DDI-DrugBank.d312.s1.e0|DDI-DrugBank.d312.s1.e1|0|null
DDI-DrugBank.d312.s1|DDI-DrugBank.d312.s1.e0|DDI-DrugBank.d312.s1.e2|0|null
DDI-DrugBank.d312.s1|DDI-DrugBank.d312.s1.e0|DDI-DrugBank.d312.s1.e3|0|null
DDI-DrugBank.d312.s1|DDI-DrugBank.d312.s1.e1|DDI-DrugBank.d312.s1.e2|0|null
DDI-DrugBank.d312.s1|DDI-DrugBank.d312.s1.e1|DDI-DrugBank.d312.s1.e3|0|null
DDI-DrugBank.d312.s1|DDI-DrugBank.d312.s1.e2|DDI-DrugBank.d312.s1.e3|0|null
DDI-DrugBank.d312.s2|DDI-DrugBank.d312.s2.e0|DDI-DrugBank.d312.s2.e1|0|null
DDI-DrugBank

DDI-DrugBank.d220.s11|DDI-DrugBank.d220.s11.e0|DDI-DrugBank.d220.s11.e4|0|null
DDI-DrugBank.d220.s11|DDI-DrugBank.d220.s11.e0|DDI-DrugBank.d220.s11.e5|0|null
DDI-DrugBank.d220.s11|DDI-DrugBank.d220.s11.e0|DDI-DrugBank.d220.s11.e6|1|advise
DDI-DrugBank.d220.s11|DDI-DrugBank.d220.s11.e1|DDI-DrugBank.d220.s11.e2|0|null
DDI-DrugBank.d220.s11|DDI-DrugBank.d220.s11.e1|DDI-DrugBank.d220.s11.e3|0|null
DDI-DrugBank.d220.s11|DDI-DrugBank.d220.s11.e1|DDI-DrugBank.d220.s11.e4|0|null
DDI-DrugBank.d220.s11|DDI-DrugBank.d220.s11.e1|DDI-DrugBank.d220.s11.e5|0|null
DDI-DrugBank.d220.s11|DDI-DrugBank.d220.s11.e1|DDI-DrugBank.d220.s11.e6|1|advise
DDI-DrugBank.d220.s11|DDI-DrugBank.d220.s11.e2|DDI-DrugBank.d220.s11.e3|0|null
DDI-DrugBank.d220.s11|DDI-DrugBank.d220.s11.e2|DDI-DrugBank.d220.s11.e4|0|null
DDI-DrugBank.d220.s11|DDI-DrugBank.d220.s11.e2|DDI-DrugBank.d220.s11.e5|0|null
DDI-DrugBank.d220.s11|DDI-DrugBank.d220.s11.e2|DDI-DrugBank.d220.s11.e6|1|advise
DDI-DrugBank.d220.s11|DDI-DrugBank.d220.s11.e3

...

DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e21|DDI-DrugBank.d484.s0.e28|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e21|DDI-DrugBank.d484.s0.e29|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e21|DDI-DrugBank.d484.s0.e30|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e21|DDI-DrugBank.d484.s0.e31|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e21|DDI-DrugBank.d484.s0.e32|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e21|DDI-DrugBank.d484.s0.e33|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e21|DDI-DrugBank.d484.s0.e34|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e21|DDI-DrugBank.d484.s0.e35|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e21|DDI-DrugBank.d484.s0.e36|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e21|DDI-DrugBank.d484.s0.e37|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e21|DDI-DrugBank.d484.s0.e38|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e21|DDI-DrugBank.d484.s0.e39|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e21|DDI-DrugBank.d484.

DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e27|DDI-DrugBank.d484.s0.e32|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e27|DDI-DrugBank.d484.s0.e33|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e27|DDI-DrugBank.d484.s0.e34|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e27|DDI-DrugBank.d484.s0.e35|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e27|DDI-DrugBank.d484.s0.e36|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e27|DDI-DrugBank.d484.s0.e37|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e27|DDI-DrugBank.d484.s0.e38|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e27|DDI-DrugBank.d484.s0.e39|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e27|DDI-DrugBank.d484.s0.e40|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e27|DDI-DrugBank.d484.s0.e41|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e27|DDI-DrugBank.d484.s0.e42|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e27|DDI-DrugBank.d484.s0.e43|0|null
DDI-DrugBank.d484.s0|DDI-DrugBank.d484.s0.e27|DDI-DrugBank.d484.

DDI-DrugBank.d456.s1|DDI-DrugBank.d456.s1.e0|DDI-DrugBank.d456.s1.e6|0|null
DDI-DrugBank.d456.s1|DDI-DrugBank.d456.s1.e0|DDI-DrugBank.d456.s1.e7|0|null
DDI-DrugBank.d456.s1|DDI-DrugBank.d456.s1.e0|DDI-DrugBank.d456.s1.e8|0|null
DDI-DrugBank.d456.s1|DDI-DrugBank.d456.s1.e0|DDI-DrugBank.d456.s1.e9|0|null
DDI-DrugBank.d456.s1|DDI-DrugBank.d456.s1.e0|DDI-DrugBank.d456.s1.e10|0|null
DDI-DrugBank.d456.s1|DDI-DrugBank.d456.s1.e0|DDI-DrugBank.d456.s1.e11|0|null
DDI-DrugBank.d456.s1|DDI-DrugBank.d456.s1.e0|DDI-DrugBank.d456.s1.e12|0|null
DDI-DrugBank.d456.s1|DDI-DrugBank.d456.s1.e0|DDI-DrugBank.d456.s1.e13|0|null
DDI-DrugBank.d456.s1|DDI-DrugBank.d456.s1.e1|DDI-DrugBank.d456.s1.e2|0|null
DDI-DrugBank.d456.s1|DDI-DrugBank.d456.s1.e1|DDI-DrugBank.d456.s1.e3|0|null
DDI-DrugBank.d456.s1|DDI-DrugBank.d456.s1.e1|DDI-DrugBank.d456.s1.e4|0|null
DDI-DrugBank.d456.s1|DDI-DrugBank.d456.s1.e1|DDI-DrugBank.d456.s1.e5|0|null
DDI-DrugBank.d456.s1|DDI-DrugBank.d456.s1.e1|DDI-DrugBank.d456.s1.e6|0|null
DDI-Drug

DDI-DrugBank.d347.s7|DDI-DrugBank.d347.s7.e1|DDI-DrugBank.d347.s7.e9|1|advise
DDI-DrugBank.d347.s7|DDI-DrugBank.d347.s7.e2|DDI-DrugBank.d347.s7.e3|0|null
DDI-DrugBank.d347.s7|DDI-DrugBank.d347.s7.e2|DDI-DrugBank.d347.s7.e4|0|null
DDI-DrugBank.d347.s7|DDI-DrugBank.d347.s7.e2|DDI-DrugBank.d347.s7.e5|0|null
DDI-DrugBank.d347.s7|DDI-DrugBank.d347.s7.e2|DDI-DrugBank.d347.s7.e6|0|null
DDI-DrugBank.d347.s7|DDI-DrugBank.d347.s7.e2|DDI-DrugBank.d347.s7.e7|0|null
DDI-DrugBank.d347.s7|DDI-DrugBank.d347.s7.e2|DDI-DrugBank.d347.s7.e8|0|null
DDI-DrugBank.d347.s7|DDI-DrugBank.d347.s7.e2|DDI-DrugBank.d347.s7.e9|1|advise
DDI-DrugBank.d347.s7|DDI-DrugBank.d347.s7.e3|DDI-DrugBank.d347.s7.e4|0|null
DDI-DrugBank.d347.s7|DDI-DrugBank.d347.s7.e3|DDI-DrugBank.d347.s7.e5|0|null
DDI-DrugBank.d347.s7|DDI-DrugBank.d347.s7.e3|DDI-DrugBank.d347.s7.e6|0|null
DDI-DrugBank.d347.s7|DDI-DrugBank.d347.s7.e3|DDI-DrugBank.d347.s7.e7|0|null
DDI-DrugBank.d347.s7|DDI-DrugBank.d347.s7.e3|DDI-DrugBank.d347.s7.e8|0|null
DDI-Drug

DDI-DrugBank.d413.s20|DDI-DrugBank.d413.s20.e1|DDI-DrugBank.d413.s20.e3|1|advise
DDI-DrugBank.d413.s20|DDI-DrugBank.d413.s20.e1|DDI-DrugBank.d413.s20.e4|1|advise
DDI-DrugBank.d413.s20|DDI-DrugBank.d413.s20.e2|DDI-DrugBank.d413.s20.e3|0|null
DDI-DrugBank.d413.s20|DDI-DrugBank.d413.s20.e2|DDI-DrugBank.d413.s20.e4|0|null
DDI-DrugBank.d413.s20|DDI-DrugBank.d413.s20.e3|DDI-DrugBank.d413.s20.e4|0|null
DDI-DrugBank.d413.s21|DDI-DrugBank.d413.s21.e0|DDI-DrugBank.d413.s21.e1|0|null
DDI-DrugBank.d413.s22|DDI-DrugBank.d413.s22.e0|DDI-DrugBank.d413.s22.e1|0|null
[('Cyclosporin', 0, 10), (':', 11, 11), ('Reports', 13, 19), ('indicate', 21, 28), ('that', 30, 33), ('cyclosporine', 35, 46), ('levels', 48, 53), ('may', 55, 57), ('be', 59, 60), ('increased', 62, 70), ('during', 72, 77), ('concomitant', 79, 89), ('treatment', 91, 99), ('with', 101, 104), ('allopurinol', 106, 116), ('sodium', 118, 123), ('for', 125, 127), ('injection', 129, 137), ('.', 138, 138)]
{'DDI-DrugBank.d413.s22.e0': ['0', '10'], 